In [2]:
import pandas as pd
from datetime import datetime, timezone, timedelta
import pytz

with open("data/output.csv", "rb") as f:
    data = pd.read_csv(f, delimiter="\t")

In [3]:
JST = pytz.timezone("Asia/Tokyo")
CST = pytz.timezone("America/Chicago")

def to_jst_timestamp(s: str, format_str="%Y-%m-%d %H:%M:%S"):
    if type(s) is not str: return None
    naive_dt = datetime.strptime(s, format_str)
    jst_dt = JST.localize(naive_dt)
    cst_dt = jst_dt.astimezone(CST)
    return cst_dt

times = data["Time Played"]
times_mapped = times.map(to_jst_timestamp)
days_played = times_mapped.groupby(times_mapped.dt.date).count()
print(days_played.sort_values(ascending=False).head(10))

Time Played
2024-03-04    30
2024-05-01    26
2024-04-13    26
2024-04-25    25
2024-04-14    24
2024-04-20    23
2024-04-18    20
2024-04-24    19
2024-03-05    17
2024-03-10    17
Name: Time Played, dtype: int64


In [28]:
records_by_level = data.loc[data["Lamp"] != "Fail"].groupby(data["Rating"])
num_clears_by_level = records_by_level["Score"].count().rename("Clears")
average_scores_by_level = records_by_level["Score"].mean().round().astype("int").rename("Average")
def max_info(group):
    max_idx = group["Score"].idxmax()
    return group.loc[max_idx][["Score", "Lamp", "Song Name"]].rename({ "Score": "Max Score", "Lamp": "Max Score Lamp", "Song Name": "Max Score Song" })
max_score_by_level = records_by_level.apply(max_info)
result = pd.merge(num_clears_by_level, average_scores_by_level, on="Rating")
result = pd.merge(result, max_score_by_level, on="Rating")
with pd.option_context('expand_frame_repr', False):
    print(result)

        Clears  Average  Max Score Max Score Lamp                          Max Score Song
Rating                                                                                   
8            7   895073     996620            GFC                       朧 (dj TAKA Remix)
9           25   918551     999650            PFC                                 Why not
10          29   921425     992160            GFC                                  隅田川夏恋歌
11          40   896780     992520            GFC                                       朧
12          56   890122     987030            GFC                          MY SUMMER LOVE
13          70   840879     978430            GFC                                Struggle
14         121   799834     943140             FC                      FUNKY SUMMER BEACH
15          26   798904     898400          Clear                             未来（ダ）FUTURE
16          16   770314     861210          Clear                      Sword of Vengeance
17        

In [38]:
# Gold 1
gold1scores = []
gold1scores.append(data[(data["Score"] >= 975000) & (data["Rating"] == 13)].head(1))
gold1scores.append(data[(data["Score"] >= 925000) & (data["Rating"] == 14)].head(1))
gold1scores.append(data[(data["Score"] >= 875000) & (data["Rating"] == 15)].head(1))
gold1scores.append(data[(data["Score"] >= 825000) & (data["Rating"] == 16)].head(1))
gold1scores.append(data[(data["Score"] >= 750000) & (data["Rating"] == 17)].head(1))
with pd.option_context('expand_frame_repr', False):
    gold1scores = pd.concat(gold1scores)
    print(gold1scores)

                              Song ID           Song Name Difficulty  Rating   Score Grade   Lamp        Time Uploaded          Time Played
40   1idIoi66ll806D8ddldOQi8bdiDO0Oil            Struggle        ESP      13  978430   AA+    GFC  2024-04-18 18:14:49  2024-04-18 18:05:47
120  9i6dOd608qb0IlqoDIPb8q1o8q1ddQQd  FUNKY SUMMER BEACH        ESP      14  943140    AA     FC  2024-05-01 22:11:00  2024-05-01 19:21:38
171  D686d06lO9IID8D0boPq0Pd8P89idO99         未来（ダ）FUTURE        ESP      15  898400   AA-  Clear  2024-04-26 01:44:41  2024-04-26 01:40:06
205  ddqO1b1ldlQd6OOoQ1boPdoboDQqd9D8  Sword of Vengeance        ESP      16  861210    A+  Clear  2024-05-01 18:42:28  2024-05-01 18:39:33
